In [1]:
#Setting up the code and installing required packages 
%load_ext autotime
from util import *
from glob import glob
import matplotlib.pyplot as plt
from shapely import wkt
from shapely.geometry import LineString, Polygon
import geopandas as gpd
from shapely.geometry import Point, LineString
import numpy as np
from shapelysmooth import taubin_smooth
pd.set_option("display.max_columns", None)

In [2]:
#Navigate to intersects shapefile and separates out the year, finds how many years from 1800 and how many years to 2100
gdf = gpd.read_file(f"Data/Merged Intersects_UniqueID/JackettIsland_Intersects.shp")
gdf["Date"] = pd.to_datetime(gdf.ShorelineI, dayfirst=True, format='mixed')
gdf["Year"] = gdf.Date.dt.year
gdf["YearsSinceBase"] = (gdf.Date - pd.Timestamp(1800, 1, 1)).dt.days / 365.25
gdf["YearsUntilFuture"] = (
    pd.Timestamp(2100, 1, 1) - gdf.Date
    ).dt.days / 365.25
gdf.Date = gdf.Date.astype(str)
gdf["TransectID"] = gdf.Unique_ID.astype(np.int64)
gdf

ShorelineI  BaselineID  Distance    IntersectX    IntersectY  \
0     04/19/2017         1.0    -97.80  1.602805e+06  5.444480e+06   
1     01/13/2000         1.0    -54.62  1.602842e+06  5.444502e+06   
2     02/19/2010         1.0    -69.27  1.602830e+06  5.444495e+06   
3     09/13/1985         1.0    -54.69  1.602842e+06  5.444502e+06   
4     02/04/1967         1.0    -65.04  1.602833e+06  5.444497e+06   
...          ...         ...       ...           ...           ...   
2337  02/22/1940         3.0    -29.51  1.603246e+06  5.444123e+06   
2338  06/25/2013         3.0   -113.28  1.603204e+06  5.444051e+06   
2339  08/28/2006         3.0   -109.38  1.603206e+06  5.444055e+06   
2340  01/31/1980         3.0   -115.24  1.603203e+06  5.444050e+06   
2341  05/19/1958         3.0    -81.24  1.603220e+06  5.444079e+06   

      Uncertaint     Unique_ID        Date  \
0           2.94  2.010001e+11  2017-04-19   
1           5.32  2.010001e+11  2000-01-13   
2           2.32  2.010001e+11  2010-02-19   
3           4.33  2.010001e+11  1985-09-13   
4           5.94  2.010001e+11  1967-04-02   
...          ...           ...         ...   
2337        3.77  2.010002e+11  1940-02-22   
2338        2.30  2.010002e+11  2013-06-25   
2339        2.32  2.010002e+11  2006-08-28   
2340        5.31  2.010002e+11  1980-01-31   
2341        5.67  2.010002e+11  1958-05-19   

                                     geometry  Year  YearsSinceBase  \
0     POINT Z (1602805.403 5444479.642 0.000)  2017      217.292266   
1     POINT Z (1602842.047 5444502.478 0.000)  2000      200.027379   
2     POINT Z (1602829.612 5444494.729 0.000)  2010      210.130048   
3     POINT Z (1602841.988 5444502.442 0.000)  1985      185.694730   
4     POINT Z (1602833.209 5444496.970 0.000)  1967      167.244353   
...                                       ...   ...             ...   
2337  POINT Z (1603246.456 5444123.385 0.000)  1940      140.136893   
2338  POINT Z (1603203.881 5444051.243 0.000)  2013      213.475702   
2339  POINT Z (1603205.860 5444054.597 0.000)  2006      206.650240   
2340  POINT Z (1603202.885 5444049.556 0.000)  1980      180.076660   
2341  POINT Z (1603220.163 5444078.833 0.000)  1958      158.373717   

      YearsUntilFuture    TransectID  
0            82.702259  201000147441  
1            99.967146  201000147441  
2            89.864476  201000147441  
3           114.299795  201000147441  
4           132.750171  201000147441  
...                ...           ...  
2337        159.857632  201000205029  
2338         86.518823  201000205029  
2339         93.344285  201000205029  
2340        119.917864  201000205029  
2341        141.620808  201000205029  

[2342 rows x 13 columns]

In [3]:
def get_transects(intersects):
  p1 = intersects.geometry[intersects.Distance.idxmin()].coords[0]
  p2 = intersects.geometry[intersects.Distance.idxmax()].coords[0]
  azimuth = math.degrees(math.atan2(p1[0]-p2[0], p1[1]-p2[1]))
  if azimuth < 0:
      azimuth += 360
  return pd.Series({"Azimuth": azimuth, "geometry": LineString([p1, p2])})

lines = gdf.groupby("TransectID")[["geometry", "Distance"]].apply(get_transects)
lines.crs = gdf.crs
lines

Azimuth                                           geometry
TransectID                                                                 
201000006218  258.690068  LINESTRING Z (1602185.330 5445755.803 0.000, 1...
201000007220  258.690068  LINESTRING Z (1602188.813 5445746.302 0.000, 1...
201000008225  258.690068  LINESTRING Z (1602192.240 5445736.789 0.000, 1...
201000009230  258.690068  LINESTRING Z (1602195.330 5445727.209 0.000, 1...
201000010239  258.690068  LINESTRING Z (1602196.461 5445717.237 0.000, 1...
...                  ...                                                ...
201000233653  274.085617  LINESTRING Z (1603305.544 5443845.332 0.000, 1...
201000234444  287.241460  LINESTRING Z (1603305.544 5443845.913 0.000, 1...
201000234674  274.085617  LINESTRING Z (1603304.318 5443835.394 0.000, 1...
201000235445  287.241459  LINESTRING Z (1603304.448 5443835.783 0.000, 1...
201000236452  287.241459  LINESTRING Z (1603300.068 5443826.672 0.000, 1...

[183 rows x 2 columns]

In [4]:
lines["dist_to_neighbour"] = lines.distance(lines.shift(-1))
breakpoints = lines.dist_to_neighbour[lines.dist_to_neighbour > 15]
lines["group"] = pd.Series(range(len(breakpoints)), index=breakpoints.index)
lines["group"] = lines.group.bfill().fillna(len(breakpoints)).astype(int)
transect_metadata = lines[["Azimuth", "group"]].to_dict(orient="index")
transect_metadata

{201000006218: {'Azimuth': 258.6900675249549, 'group': 0},
 201000007220: {'Azimuth': 258.69006752786225, 'group': 0},
 201000008225: {'Azimuth': 258.6900681804391, 'group': 0},
 201000009230: {'Azimuth': 258.6900675252886, 'group': 0},
 201000010239: {'Azimuth': 258.6900675268282, 'group': 0},
 201000012112: {'Azimuth': 238.55128489231237, 'group': 1},
 201000013122: {'Azimuth': 238.55128571432044, 'group': 1},
 201000014130: {'Azimuth': 238.55128432263012, 'group': 1},
 201000015137: {'Azimuth': 238.55128432319822, 'group': 1},
 201000016143: {'Azimuth': 238.5512843218965, 'group': 1},
 201000017149: {'Azimuth': 238.55128489223875, 'group': 1},
 201000018155: {'Azimuth': 238.55128628350332, 'group': 1},
 201000019161: {'Azimuth': 238.5512843217919, 'group': 1},
 201000019767: {'Azimuth': 245.07152607707573, 'group': 1},
 201000020767: {'Azimuth': 245.0715260770204, 'group': 1},
 201000021767: {'Azimuth': 245.071526077383, 'group': 1},
 201000022768: {'Azimuth': 245.07152547213863, 'g

In [118]:
#Linear regression is run here. See util.py for the breakdown on linear_models
linear_models = fit(gdf, transect_metadata)
linear_models

TransectID     slope   intercept  group  r2_score        mae  \
0      200003642104 -0.318547   25.285025      0  0.960654   1.115822   
1      200003643105 -0.366127   32.494345      0  0.910309   1.740924   
2      200003644109 -0.356978   28.404856      0  0.865506   2.194500   
3      200003644776 -0.313893   20.538294      0  0.756386   2.438031   
4      200003645776 -0.207140    2.383278      0  0.645326   2.797733   
...             ...       ...         ...    ...       ...        ...   
86217  200541649478 -1.532451  240.232377   1767  0.793650  16.785859   
86218  200541650479 -1.494222  234.715230   1767  0.807904  15.651756   
86219  200541651480 -1.477228  232.926611   1767  0.823446  14.693894   
86220  200541652481 -1.488089  236.032817   1767  0.839876  13.957826   
86221  200541653483 -1.472323  233.424946   1767  0.842013  13.700079   

              mse       rmse  
0        1.989394   1.410459  
1        6.322166   2.514392  
2        9.478906   3.078783  
3       15.190291   3.897472  
4       11.288139   3.359783  
...           ...        ...  
86217  325.524645  18.042302  
86218  283.023731  16.823309  
86219  249.442552  15.793750  
86220  225.077591  15.002586  
86221  216.841716  14.725546  

[86222 rows x 8 columns]

In [8]:
#Only run if rolling average is needed. Otherwise SKIP THIS
#linear_models = fit(gdf, transect_metadata)
#rolled_slopes = linear_models.groupby("group").slope.rolling(10, min_periods=1).mean().dropna().reset_index(level=0)
#linear_models.slope = rolled_slopes.slope
#linear_models.dropna(inplace=True)
#linear_models

time: 361 µs (started: 2024-08-07 16:42:36 +12:00)


In [119]:
#Coordinates of the projected shoreline are plotted here

#Changed coordinate function by making old_x and old_y negative 
def calculate_new_coordinates(old_x, old_y, bearing, distance):
    bearing_radians = math.radians(bearing)
    new_x = old_x + (distance * math.sin(bearing_radians))
    new_y = old_y + (distance * math.cos(bearing_radians))
    point = Point(new_x, new_y)
    assert not point.is_empty
    return point

#Removed other model equations and changed Azimuth addtion from 180 to 360 deg
def predict(
    df: pd.DataFrame,
    linear_models: pd.DataFrame,
    transect_metadata: dict,
):
    """_summary_

    Args:
        df (pd.DataFrame): dataframe with columns: TransectID, Date, Distance, YearsSinceBase
        linear_models (pd.DataFrame): dataframe with columns: TransectID, slope, intercept
        transect_metadata (dict): dict lookup of TransectID to Azimuth & group
        
    Returns:
        pd.DataFrame: resulting prediction points for the year 2100
    """
    results = []
    for i, row in linear_models.iterrows():
        transect_ID = row.TransectID
        transect_df = df[df.TransectID == transect_ID]
        latest_row = transect_df[transect_df.Date == transect_df["Date"].max()].iloc[0]
        future_year = int(row.get("FUTURE_YEAR", FUTURE_YEAR))
        result = row.to_dict()
        result.update({
            "TransectID": transect_ID,
            "BaselineID": latest_row.BaselineID,
            "group": row.group,
            "Year": future_year,
            "ocean_point": calculate_new_coordinates(
                latest_row.geometry.x,
                latest_row.geometry.y,
                transect_metadata[transect_ID]["Azimuth"] + 180,
                500,
            ),
        })
        
        model = "linear"
        slope = row.slope
        intercept = row.intercept

        predicted_distance = slope * (future_year - 1800) + intercept
        distance_difference = latest_row.Distance - predicted_distance
        result[f"{model}_model_point"] = calculate_new_coordinates(
            latest_row.geometry.x,
            latest_row.geometry.y,
            transect_metadata[transect_ID]["Azimuth"],
            distance_difference,
        )
        result[f"{model}_model_predicted_distance"] = predicted_distance
        result[f"{model}_model_distance"] = distance_difference
        results.append(result)
    results = gpd.GeoDataFrame(results)
    return results

In [120]:
#Projection file is created here with the stats and coordinate points in table format
results = predict(gdf, linear_models, transect_metadata)
results

TransectID     slope   intercept   group  r2_score        mae  \
0      2.000036e+11 -0.318547   25.285025     0.0  0.960654   1.115822   
1      2.000036e+11 -0.366127   32.494345     0.0  0.910309   1.740924   
2      2.000036e+11 -0.356978   28.404856     0.0  0.865506   2.194500   
3      2.000036e+11 -0.313893   20.538294     0.0  0.756386   2.438031   
4      2.000036e+11 -0.207140    2.383278     0.0  0.645326   2.797733   
...             ...       ...         ...     ...       ...        ...   
86217  2.005416e+11 -1.532451  240.232377  1767.0  0.793650  16.785859   
86218  2.005417e+11 -1.494222  234.715230  1767.0  0.807904  15.651756   
86219  2.005417e+11 -1.477228  232.926611  1767.0  0.823446  14.693894   
86220  2.005417e+11 -1.488089  236.032817  1767.0  0.839876  13.957826   
86221  2.005417e+11 -1.472323  233.424946  1767.0  0.842013  13.700079   

              mse       rmse  BaselineID  Year  \
0        1.989394   1.410459         1.0  2100   
1        6.322166   2.514392         1.0  2100   
2        9.478906   3.078783         1.0  2100   
3       15.190291   3.897472         1.0  2100   
4       11.288139   3.359783         1.0  2100   
...           ...        ...         ...   ...   
86217  325.524645  18.042302         1.0  2100   
86218  283.023731  16.823309         1.0  2100   
86219  249.442552  15.793750         1.0  2100   
86220  225.077591  15.002586         1.0  2100   
86221  216.841716  14.725546         1.0  2100   

                                        ocean_point  \
0      POINT (1577899.0126842926 5513464.801424051)   
1       POINT (1577889.6904829284 5513460.86961325)   
2      POINT (1577880.6282009052 5513456.515422609)   
3       POINT (1577820.1795547206 5513423.97894378)   
4       POINT (1577812.048512659 5513417.673071384)   
...                                             ...   
86217  POINT (1523651.0817387495 5430884.520312319)   
86218  POINT (1523649.5970341577 5430895.061726855)   
86219  POINT (1523649.2099960125 5430905.369076312)   
86220  POINT (1523650.2537103635 5430915.371338842)   
86221   POINT (1523651.297425778 5430925.373605757)   

                                 linear_model_point  \
0        POINT (1577624.13447869 5513911.490075701)   
1      POINT (1577611.9169112307 5513912.263356664)   
2      POINT (1577602.6948723772 5513908.168777583)   
3      POINT (1577604.7736542688 5513904.036110803)   
4      POINT (1577601.3263102947 5513887.292017656)   
...                                             ...   
86217   POINT (1524245.373879372 5430757.796259782)   
86218   POINT (1524241.638235402 5430768.817648004)   
86219  POINT (1524240.4887868715 5430779.287570262)   
86220   POINT (1524242.727534587 5430789.035009503)   
86221  POINT (1524242.7327220584 5430799.258720192)   

       linear_model_predicted_distance  linear_model_distance  
0                           -70.279065              24.489065  
1                           -77.343650              30.013650  
2                           -78.688478              30.318478  
3                           -73.629731              26.169731  
4                           -59.758862              14.728862  
...                                ...                    ...  
86217                      -219.502972             107.652972  
86218                      -213.551428             105.351428  
86219                      -210.241877             104.571877  
86220                      -210.393777             105.793777  
86221                      -208.271903             104.731903  

[86222 rows x 14 columns]

In [121]:
#Spatial reference added to the results
results.set_geometry("linear_model_point", inplace=True, crs=2193)
results

TransectID     slope   intercept   group  r2_score        mae  \
0      2.000036e+11 -0.318547   25.285025     0.0  0.960654   1.115822   
1      2.000036e+11 -0.366127   32.494345     0.0  0.910309   1.740924   
2      2.000036e+11 -0.356978   28.404856     0.0  0.865506   2.194500   
3      2.000036e+11 -0.313893   20.538294     0.0  0.756386   2.438031   
4      2.000036e+11 -0.207140    2.383278     0.0  0.645326   2.797733   
...             ...       ...         ...     ...       ...        ...   
86217  2.005416e+11 -1.532451  240.232377  1767.0  0.793650  16.785859   
86218  2.005417e+11 -1.494222  234.715230  1767.0  0.807904  15.651756   
86219  2.005417e+11 -1.477228  232.926611  1767.0  0.823446  14.693894   
86220  2.005417e+11 -1.488089  236.032817  1767.0  0.839876  13.957826   
86221  2.005417e+11 -1.472323  233.424946  1767.0  0.842013  13.700079   

              mse       rmse  BaselineID  Year  \
0        1.989394   1.410459         1.0  2100   
1        6.322166   2.514392         1.0  2100   
2        9.478906   3.078783         1.0  2100   
3       15.190291   3.897472         1.0  2100   
4       11.288139   3.359783         1.0  2100   
...           ...        ...         ...   ...   
86217  325.524645  18.042302         1.0  2100   
86218  283.023731  16.823309         1.0  2100   
86219  249.442552  15.793750         1.0  2100   
86220  225.077591  15.002586         1.0  2100   
86221  216.841716  14.725546         1.0  2100   

                                        ocean_point  \
0      POINT (1577899.0126842926 5513464.801424051)   
1       POINT (1577889.6904829284 5513460.86961325)   
2      POINT (1577880.6282009052 5513456.515422609)   
3       POINT (1577820.1795547206 5513423.97894378)   
4       POINT (1577812.048512659 5513417.673071384)   
...                                             ...   
86217  POINT (1523651.0817387495 5430884.520312319)   
86218  POINT (1523649.5970341577 5430895.061726855)   
86219  POINT (1523649.2099960125 5430905.369076312)   
86220  POINT (1523650.2537103635 5430915.371338842)   
86221   POINT (1523651.297425778 5430925.373605757)   

                    linear_model_point  linear_model_predicted_distance  \
0      POINT (1577624.134 5513911.490)                       -70.279065   
1      POINT (1577611.917 5513912.263)                       -77.343650   
2      POINT (1577602.695 5513908.169)                       -78.688478   
3      POINT (1577604.774 5513904.036)                       -73.629731   
4      POINT (1577601.326 5513887.292)                       -59.758862   
...                                ...                              ...   
86217  POINT (1524245.374 5430757.796)                      -219.502972   
86218  POINT (1524241.638 5430768.818)                      -213.551428   
86219  POINT (1524240.489 5430779.288)                      -210.241877   
86220  POINT (1524242.728 5430789.035)                      -210.393777   
86221  POINT (1524242.733 5430799.259)                      -208.271903   

       linear_model_distance  
0                  24.489065  
1                  30.013650  
2                  30.318478  
3                  26.169731  
4                  14.728862  
...                      ...  
86217             107.652972  
86218             105.351428  
86219             104.571877  
86220             105.793777  
86221             104.731903  

[86222 rows x 14 columns]

In [122]:
#Line and polygon shapefiles are created here 
def prediction_results_to_line_polygon(results: gpd.GeoDataFrame):
    lines = []
    polygons = []
    for group_name, group_data in results.groupby(["BaselineID", "group"]):
        if len(group_data) > 1:
            # Convert the points to LineString
            line = LineString(list(group_data.geometry))
            lines.append(line)
            # Convert the points to a closed Polygon
            polygon = Polygon(list(group_data.geometry) + list(group_data.ocean_point)[::-1])
            polygons.append(polygon)
    lines = gpd.GeoSeries(lines, crs=2193)
    polygons = gpd.GeoSeries(polygons, crs=2193)
    return lines, polygons
lines, poly = prediction_results_to_line_polygon(results)

In [123]:
m = lines.explore()
lines.apply(lambda line: taubin_smooth(line, steps=500)).to_file("Projections/SouthIsland_output_line_smoothed.shp")
lines.apply(lambda line: taubin_smooth(line, steps=500)).explore(m=m, color="red")

In [15]:
#Saving line and polygon projection file to Z drive. Change file location accordingly  
lines, poly = prediction_results_to_line_polygon(results)
lines.to_file("Z:\Lalita\RNC Cont\......\BigBay_projection_output_lines.shp")
poly.to_file("Z:\Lalita\RNC Cont\.......\BigBay_projection_output_polygon.shp")

DriverIOError: Failed to create file Z:\Lalita\RNC Cont\....../BigBay_projection_output_lines.shp: No such file or directory

time: 859 ms (started: 2024-08-07 16:42:39 +12:00)


In [70]:
#Saving line and polygon projection file to folder in VS Code. Change file location accordingly
lines, poly = prediction_results_to_line_polygon(results)
lines.to_file("Projections/WaihekeIsland_projection_output_line.shp")
poly.to_file("Projections/WaihekeIsland_projection_output_polygon.shp")

In [ ]:
#Quick visualisation of projected polygon and historic shorelines 
m = poly.explore(tiles="Esri.WorldImagery")
gpd.GeoDataFrame(results.drop(columns=["ocean_point", "linear_model_point"]), geometry=results.linear_model_point).explore(m=m)
gdf.explore("Year", legend=True, m=m)